In [3]:
import dask.dataframe as dd
import dask.distributed
import numpy as np
import pandas as pd

In [4]:
df0 = pd.read_csv('yellow_tripdata_2015-01.csv')

In [5]:
df0.dropna(inplace = True)

In [6]:
df0

VendorID tpep_pickup_datetime tpep_dropoff_datetime  \
0                2  2015-01-15 19:05:39   2015-01-15 19:23:42   
1                1  2015-01-10 20:33:38   2015-01-10 20:53:28   
2                1  2015-01-10 20:33:38   2015-01-10 20:43:41   
3                1  2015-01-10 20:33:39   2015-01-10 20:35:31   
4                1  2015-01-10 20:33:39   2015-01-10 20:52:58   
...            ...                  ...                   ...   
12748981         1  2015-01-10 19:01:44   2015-01-10 19:05:40   
12748982         1  2015-01-10 19:01:44   2015-01-10 19:07:26   
12748983         1  2015-01-10 19:01:44   2015-01-10 19:15:01   
12748984         1  2015-01-10 19:01:44   2015-01-10 19:17:03   
12748985         1  2015-01-10 19:01:45   2015-01-10 19:07:33   

          passenger_count  trip_distance  pickup_longitude  pickup_latitude  \
0                       1           1.59        -73.993896        40.750111   
1                       1           3.30        -74.001648        40.724243   
2                       1           1.80        -73.963341        40.802788   
3                       1           0.50        -74.009087        40.713818   
4                       1           3.00        -73.971176        40.762428   
...                   ...            ...               ...              ...   
12748981                2           1.00        -73.951988        40.786217   
12748982                2           0.80        -73.982742        40.728184   
12748983                1           3.40        -73.979324        40.749550   
12748984                1           1.30        -73.999565        40.738483   
12748985                1           0.70        -73.960350        40.766399   

          RateCodeID store_and_fwd_flag  dropoff_longitude  dropoff_latitude  \
0                  1                  N         -73.974785         40.750618   
1                  1                  N         -73.994415         40.759109   
2                  1                  N         -73.951820         40.824413   
3                  1                  N         -74.004326         40.719986   
4                  1                  N         -74.004181         40.742653   
...              ...                ...                ...               ...   
12748981           1                  N         -73.953735         40.775162   
12748982           1                  N         -73.974976         40.720013   
12748983           1                  N         -73.969101         40.787800   
12748984           1                  N         -73.981819         40.737652   
12748985           1                  N         -73.968643         40.760777   

          payment_type  fare_amount  extra  mta_tax  tip_amount  tolls_amount  \
0                    1         12.0    1.0      0.5        3.25           0.0   
1                    1         14.5    0.5      0.5        2.00           0.0   
2                    2          9.5    0.5      0.5        0.00           0.0   
3                    2          3.5    0.5      0.5        0.00           0.0   
4                    2         15.0    0.5      0.5        0.00           0.0   
...                ...          ...    ...      ...         ...           ...   
12748981             1          5.5    0.0      0.5        1.25           0.0   
12748982             1          6.0    0.0      0.5        2.00           0.0   
12748983             2         13.5    0.0      0.5        0.00           0.0   
12748984             1         10.5    0.0      0.5        2.25           0.0   
12748985             2          5.5    0.0      0.5        0.00           0.0   

          improvement_surcharge  total_amount  
0                           0.3         17.05  
1                           0.3         17.80  
2                           0.3         10.80  
3                           0.3          4.80  
4                           0.3         16.30  
...                         ...           ...  
12748981  

In [7]:
df1 = df0[['pickup_longitude','pickup_latitude','dropoff_longitude','dropoff_latitude','total_amount']]

In [8]:
df1

pickup_longitude  pickup_latitude  dropoff_longitude  \
0               -73.993896        40.750111         -73.974785   
1               -74.001648        40.724243         -73.994415   
2               -73.963341        40.802788         -73.951820   
3               -74.009087        40.713818         -74.004326   
4               -73.971176        40.762428         -74.004181   
...                    ...              ...                ...   
12748981        -73.951988        40.786217         -73.953735   
12748982        -73.982742        40.728184         -73.974976   
12748983        -73.979324        40.749550         -73.969101   
12748984        -73.999565        40.738483         -73.981819   
12748985        -73.960350        40.766399         -73.968643   

          dropoff_latitude  total_amount  
0                40.750618         17.05  
1                40.759109         17.80  
2                40.824413         10.80  
3                40.719986          4.80  
4                40.742653         16.30  
...                    ...           ...  
12748981         40.775162          7.55  
12748982         40.720013          8.80  
12748983         40.787800         14.30  
12748984         40.737652         13.55  
12748985         40.760777          6.30  

[12748983 rows x 5 columns]

In [9]:
df1.to_parquet('output.parquet')

In [10]:
df = dd.read_parquet('output.parquet', engine='fastparquet', index='pickup_datetime')

In [11]:
df

Dask DataFrame Structure:
              pickup_longitude pickup_latitude dropoff_longitude dropoff_latitude total_amount
npartitions=1                                                                                 
                       float64         float64           float64          float64      float64
                           ...             ...               ...              ...          ...
Dask Name: read-parquet, 1 tasks

In [12]:
df = df[df.pickup_latitude.notnull() & df.pickup_longitude.notnull() 
        & ((df.pickup_latitude - 40.75).abs() <= 0.5) 
        & ((df.pickup_longitude + 73.9).abs() <= 0.5)
       ]
df = df[df.dropoff_latitude.notnull() & df.dropoff_longitude.notnull() 
        & ((df.dropoff_latitude - 40.75).abs() <= 0.5) 
        & ((df.dropoff_longitude + 73.9).abs() <= 0.5)
       ]

In [13]:
df.count().compute()

pickup_longitude     12483188
pickup_latitude      12483188
dropoff_longitude    12483188
dropoff_latitude     12483188
total_amount         12483188
dtype: int64

In [14]:
df.head()

pickup_longitude  pickup_latitude  dropoff_longitude  \
pickup_datetime                                                         
0.0                    -73.993896        40.750111         -73.974785   
0.0                    -74.001648        40.724243         -73.994415   
0.0                    -73.963341        40.802788         -73.951820   
0.0                    -74.009087        40.713818         -74.004326   
0.0                    -73.971176        40.762428         -74.004181   

                 dropoff_latitude  total_amount  
pickup_datetime                                  
0.0                     40.750618         17.05  
0.0                     40.759109         17.80  
0.0                     40.824413         10.80  
0.0                     40.719986          4.80  
0.0                     40.742653         16.30

In [15]:
def convert_lon(d, latvar):
    "Convert longitude to web mercator"
    k = d[latvar].copy()
    k = (20037508.34 / 180) * (np.log(np.tan((90. + d[latvar]) * np.pi/360))/(np.pi/180.))
    return k

In [16]:
df['pickup_longitude'] = df.pickup_longitude * (20037508.34 / 180)
df['pickup_latitude'] = df.map_partitions(convert_lon, 'pickup_latitude')
df['dropoff_longitude'] = df.dropoff_longitude * (20037508.34 / 180)
df['dropoff_latitude'] = df.map_partitions(convert_lon, 'dropoff_latitude')

In [17]:
import datashader as ds
import datashader.transfer_functions as tf

import datashader as ds
from datashader.bokeh_ext import InteractiveImage
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno
from IPython.core.display import HTML, display

In [29]:
from bokeh.models import BoxZoomTool
from bokeh.plotting import figure, output_notebook, show
from bokeh.io import output_file, show

output_file("TaxiFireflies.html")
output_notebook()

#set centers, bounds, and ranges in web mercator coords
x_center = -8234000 
y_center = 4973000

x_half_range = 30000
y_half_range = 25000

NYC = x_range, y_range = ((x_center - x_half_range, x_center + x_half_range), 
                          (y_center-y_half_range, y_center+y_half_range))

# plot_width scales (quadratically?) with memory consumption.
# With 32GB RAM, I can set this to 2000, but 2500 crashes with MemoryError.
# I used this setting for high quality, large plots. 
# plot_width = 2000 

# plot_width of 400 seems to require less than 4GB, and makes the notebook more manageable. 
# Also changes aesthetic appearance by decreasing GPS "noise" due to coarse binning
plot_width  = 300 

# auto calculate from width
plot_height = int(plot_width/(x_half_range/y_half_range))

def base_plot(tools='pan,wheel_zoom,reset,save',plot_width=plot_width, 
              plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0, **plot_args)
    
    p.axis.visible = False
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    
    p.add_tools(BoxZoomTool(match_aspect=True))
    
    return p
    
options = dict(line_color=None, fill_color='blue', size=5)

Loading BokehJS ...

In [19]:
background = "black"
export = partial(export_image, export_path="export", background=background)
cm = partial(colormap_select, reverse=(background=="black"))


def create_image_1(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'pickup_longitude', 'pickup_latitude', ds.count('total_amount'))
    img = tf.shade(agg, cmap=viridis, how='eq_hist')
    return tf.dynspread(img, threshold=0.5, max_px=4)

In [20]:
p = base_plot(background_fill_color=background)
export(create_image_1(x_range, y_range, plot_width, plot_height),"pickups_large_wide")
InteractiveImage(p, create_image_1)

In [21]:
background = "black"
export = partial(export_image, export_path="export", background=background)
cm = partial(colormap_select, reverse=(background=="black"))


def create_image_2(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'dropoff_longitude', 'dropoff_latitude', ds.count('total_amount'))
    img = tf.shade(agg, cmap=inferno, how='eq_hist')
    return tf.dynspread(img, threshold=0.5, max_px=4)

In [22]:
p = base_plot(background_fill_color=background)
export(create_image_2(x_range, y_range, plot_width, plot_height),"dropoffs_large_wide")
InteractiveImage(p, create_image_2)

In [23]:
background = 'black'
export = partial(export_image, export_path="export", background=background)
cm = partial(colormap_select, reverse=(background=="black"))


def create_image_3(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    drops = cvs.points(df, 'dropoff_longitude', 'dropoff_latitude', ds.count('total_amount'))
    picks = cvs.points(df, 'pickup_longitude', 'pickup_latitude', ds.count('total_amount'))
    more_drops = tf.shade(drops.where(drops > picks), cmap=inferno, how='eq_hist')
    more_picks = tf.shade(picks.where(picks > drops), cmap=viridis,  how='eq_hist')
    img = tf.stack(more_picks,more_drops)
    return tf.dynspread(img, threshold=0.5, max_px=4)

In [30]:
p = base_plot(background_fill_color=background)
export(create_image_3(x_range, y_range, plot_width, plot_height),"pickups_dropoffs_large_wide")
InteractiveImage(p, create_image_3)

MemoryError: 